In [1]:
import matplotlib
#matplotlib.use('Agg')

In [2]:
from scipy import signal
import os
import datetime
import time
import copy
import shutil
import sys
sys.path.append('/mnt/nfs/d50/pastel/USERS/lecestres/analyse/')

from function_read import *
#from data.set_output_name import *
#from forecast_veri import *
#from data.aux_and_plot import *
import numpy as np
from mpl_toolkits.axes_grid1 import make_axes_locatable
import matplotlib.pyplot as plt
from mpl_toolkits.basemap import Basemap, shiftgrid
from scipy.stats import gaussian_kde

import calendar
import locale
locale.setlocale( locale.LC_ALL , 'en_US' )
from netCDF4 import num2date, date2num

from joblib import Parallel, delayed
import joblib

from HWMI import *

In [3]:
### EXPERIENCE NAME
#expname = "ocean_reanalysis_GREP"
expname = "sst_retroprevision_sys7"

### PERCENTILE THRESHOLD
percent_thresh = 95
#percent_thresh = 90

### MINIMAL DURATION OF A HW
duration_min = 5
#duration_min = 3

### REGION OF EXPERIENCE

#reg_name = 'north_pacific'
#reg_name = 'north_atlantic'
#reg_name = 'indian_ocean'
#reg_name = 'austral_ocean'
#reg_name = 'tropical_atlantic'
#reg_name = 'tropical_pacific'
#reg_name = 'mediterranee'
reg_name = 'global'

if reg_name == 'north_pacific':
    lats_bnds = np.array([30,65])
    lons_bnds = np.array([120, -120])
if reg_name == 'north_atlantic':
    lats_bnds = np.array([30,65])
    lons_bnds = np.array([-80, 0])
if reg_name == 'indian_ocean':
    lats_bnds = np.array([-30,30])
    lons_bnds = np.array([45, 110])
if reg_name == 'austral_ocean':
    lats_bnds = np.array([-90,-30])
    lons_bnds = np.array([-180, 180])
if reg_name == 'tropical_atlantic':
    lats_bnds = np.array([-30,30])
    lons_bnds = np.array([-70, 20])
if reg_name == 'tropical_pacific':
    lats_bnds = np.array([-30,30])
    lons_bnds = np.array([120, -70])
if reg_name == 'mediterranee':
    lats_bnds = np.array([30,50])
    lons_bnds = np.array([-5, 40])
if reg_name == 'global':
    lats_bnds = np.array([-90,90])
    lons_bnds = np.array([-180,180])

nlat = lats_bnds[1]-lats_bnds[0]
if lons_bnds[1]<lons_bnds[0]:
    nlon = lons_bnds[1]%360-lons_bnds[0]
else:
    nlon = lons_bnds[1]-lons_bnds[0]
#print('nlon : ', nlon)

### YEARS
if expname == 'ocean_reanalysis_GREP':
    end_year=2016
    start_year=1993
elif expname == 'sst_retroprevision_sys7':
    end_year=2016
    start_year=1993
nyear=end_year-start_year+1

### SEASON
#season = "NDJFMAM"
season = "DJF"
if season == 'NDJFMAM':
    nday = 211
    season_start_day = [11,1] #1stNov
    season_end_day = [5,31] #31stMay
    first_day = 0
    
elif season == 'DJF':
    nday = 90
    season_start_day = [12,1] #1stDec
    season_end_day = [3,1] #1stMarch
    first_day = 30
    
ndayseas = nday//duration_min +1

if expname == "ocean_reanalysis_GREP":
    ### NAME OF VARIABLE IN THE NC FILE
    varname = 'thetao_mean'
    
    ### NUMBER OF MEMBS
    first_memb = 0
    last_memb = 1
    nmemb = last_memb-first_memb
    
    ### CROSS VALIDATION
    cv = True
    if cv:
        cv_str = "CV"
    else:
        cv_str = 'notCV'
        
elif expname == "sst_retroprevision_sys7":
    ### NAME OF VARIABLE IN THE NC FILE
    varname = 'sst'
    
    ### NUMBER OF MEMBS
    first_memb = 0
    last_memb = 2
    nmemb = last_memb-first_memb
    
    ### CROSS VALIDATION
    cv = True
    if cv:
        cv_str = "CV"
    else:
        cv_str = 'notCV'

### PARAMETERS
# Will be initialized later in the export
# parameters_str = reg_name + "_" + season + "_" + cv_str + '_percent%i'%(percent_thresh) + '_daymin%i'%(duration_min) +  "ref%i-%i"%(start_year, end_year)

In [4]:
time_start = time.time()

if expname == "ocean_reanalysis_GREP":
    fileGrep = "/cnrm/pastel/USERS/lecestres/NO_SAVE/data/ocean_reanalysis_GREP/sst_GREP_1d_199301_201812.nc"
    varf = netCDF4.Dataset(fileGrep)
    x0,x1 = lons_bnds[0], lons_bnds[1]
    cross_greenwich = (x0<0 and x1>0)
    if x0<0:
        x0=x0+360
    if x1<=0:
        x1=x1+360
    y0,y1 = lats_bnds[0], lats_bnds[1]
    y_down,y_up = 90-y0, 90-y1
    lats_reg = varf.variables['lat'][y0+90:y1+90]
    if cross_greenwich:
        lons_reg_W = varf.variables['lon'][x0:360]
        lons_reg_E = varf.variables['lon'][0:x1]
        lons_reg=np.ma.concatenate((lons_reg_W, lons_reg_E))
    else:
        lons_reg = varf.variables['lon'][x0:x1]
        
    target=np.ma.zeros((nyear, nday, nmemb, nlat, nlon))
    for j,jmemb in enumerate(range(first_memb, last_memb)):
        for i,iyear in enumerate(range(start_year, end_year+1)):
            #print(i, iyear)
            i_start_day = (date(iyear,season_start_day[0], season_start_day[1])-date(start_year,1,1)).days
            i_end_day = (date(iyear+1,season_end_day[0], season_end_day[1])-date(start_year,1,1)).days
            
            if cross_greenwich:
                #print(x0,x1)
                target_W=varf.variables[varname][i_start_day:i_end_day,jmemb,:,x0:360][:nday,:,:]
                target_E=varf.variables[varname][i_start_day:i_end_day,jmemb,:,0:x1][:nday,:,:]
                #print(target_W.shape, target_E.shape)
                target_lon=np.flip(np.ma.concatenate((target_W,target_E), axis=2), axis=1)
            else:
                target_lon=np.flip(varf.variables[varname][i_start_day:i_end_day,jmemb,:,x0:x1][:nday,:,:],axis=1)
            target[i,:,j,:,:]=target_lon[:,y_up:y_down,:]
            print((j*nyear+i+1)/(nyear*nmemb)*100, ' % done after : ', time.time()-time_start)
             
elif expname == "sst_retroprevision_sys7":
    pathPrevi = "/cnrm/pastel/DATA/sys7/series/sst/HK/"
    files = glob(pathPrevi+"*.nc")
    files.sort()
    target = np.ma.zeros((nyear, nday, nmemb, nlat, nlon))
    for i,iyear in enumerate(range(start_year, end_year+1)):
        varf = netCDF4.Dataset(files[i])
        vararray, lats_reg, lons_reg = extract_array(varf, varname, nday,  np.array(lons_bnds), np.array(lats_bnds), start_time = first_day)
        varf.close()
        for j,jmemb in enumerate(range(first_memb, last_memb)):
            target[i,:,j,:,:] = vararray[:,jmemb,:,:]    
            target.mask[i,:,j,:,:] = vararray.mask[:,jmemb,:,:]
            print((i*nmemb+j+1)/(nyear*nmemb)*100, ' % done after : ', time.time()-time_start)

2.083333333333333  % done after :  7.021741628646851
4.166666666666666  % done after :  7.0384252071380615
6.25  % done after :  14.015048265457153
8.333333333333332  % done after :  14.030818462371826
10.416666666666668  % done after :  23.328958749771118
12.5  % done after :  23.344722747802734
14.583333333333334  % done after :  31.94381594657898
16.666666666666664  % done after :  31.95924711227417
18.75  % done after :  38.96963715553284
20.833333333333336  % done after :  38.98460006713867
22.916666666666664  % done after :  46.122549533843994
25.0  % done after :  46.137593030929565
27.083333333333332  % done after :  53.20538377761841
29.166666666666668  % done after :  53.22032308578491
31.25  % done after :  60.20711088180542
33.33333333333333  % done after :  60.22195363044739
35.41666666666667  % done after :  67.32556295394897
37.5  % done after :  67.34066224098206
39.58333333333333  % done after :  74.33389353752136
41.66666666666667  % done after :  74.34889912605286
43

In [5]:
HWMI = np.zeros((nyear,nmemb,nlat,nlon))
HW = np.zeros((nyear,nmemb,nday,nlat,nlon))
ndayexedthreshold = np.zeros((nyear,nmemb,nlat,nlon))
DDthreshold = np.zeros((nyear,nmemb,nlat,nlon))
fitsubHWarray = np.zeros((nyear, ndayseas, nmemb, nlat, nlon))
subHWarray = np.zeros((nyear, ndayseas, nmemb, nlat, nlon))
impossible_fit_list = []
sstMeanarray = np.zeros((nyear,nmemb,nlat,nlon))

def parallelized_HWMIs_computation(ilat, ilon):    #, HWMI, ndayexedthreshold, DDthreshold, fitsubHWarray, subHWarray):
    if target.mask[0,0,0,ilat,ilon] == False: #Confirm offshore
        HWMIyear, HWlstyear, HWstartmembyear, HWendmembyear, ndayexedthresholdyear, DDthresholdyear, subHWarrayyear, fitsubHWarrayyear, sstMeanarrayyear, impossible_fit = calc_HWMIyear(target[:,:,:,ilat,ilon], cross_valid = cv, percent_thresh = percent_thresh, duration_min = duration_min)
        #print HWMIyear
        HWMI[:,:,ilat,ilon]=np.array(HWMIyear)
        ndayexedthreshold[:,:,ilat,ilon]=np.array(ndayexedthresholdyear)
        DDthreshold[:,:,ilat,ilon]=np.array(DDthresholdyear)
        fitsubHWarray[:,:, :, ilat,ilon]=np.array(fitsubHWarrayyear)
        subHWarray[:,:, :, ilat,ilon]=np.array(subHWarrayyear)
        sstMeanarray[:,:,ilat,ilon]=np.array(sstMeanarrayyear)
        impossible_fit_list.append((impossible_fit,ilat,ilon))
    return()

Parallel(n_jobs=-1, timeout = 5*3600, verbose = 20, require='sharedmem', mmap_mode='w+')(delayed(parallelized_HWMIs_computation)(ilat, ilon) for ilat in range(nlat) for ilon in range(nlon))

HWMI=np.ma.array(HWMI, mask = target.mask[:,0,:,:,:] )
ndayexedthreshold=np.ma.array(ndayexedthreshold, mask = target.mask[:,0,:,:,:] )
fitsubHWarray=np.ma.array(fitsubHWarray, mask = target.mask[:,0:(ndayseas),:,:,:] )
subHWarray=np.ma.array(subHWarray, mask = target.mask[:,0:(ndayseas),:,:,:])
sstMeanarray=np.ma.array(sstMeanarray, mask = target.mask[:,0,:,:,:])

[Parallel(n_jobs=-1)]: Using backend ThreadingBackend with 12 concurrent workers.
[Parallel(n_jobs=-1)]: Done   1 tasks      | elapsed:    0.8s
[Parallel(n_jobs=-1)]: Done   2 tasks      | elapsed:    0.8s
[Parallel(n_jobs=-1)]: Done   3 tasks      | elapsed:    0.8s
[Parallel(n_jobs=-1)]: Done   4 tasks      | elapsed:    0.8s
[Parallel(n_jobs=-1)]: Done   5 tasks      | elapsed:    0.8s
[Parallel(n_jobs=-1)]: Done   6 tasks      | elapsed:    0.8s
[Parallel(n_jobs=-1)]: Done   7 tasks      | elapsed:    0.9s
[Parallel(n_jobs=-1)]: Done   8 tasks      | elapsed:    0.9s
[Parallel(n_jobs=-1)]: Done   9 tasks      | elapsed:    0.9s
[Parallel(n_jobs=-1)]: Done  10 tasks      | elapsed:    0.9s
[Parallel(n_jobs=-1)]: Done  11 tasks      | elapsed:    0.9s
[Parallel(n_jobs=-1)]: Done  12 tasks      | elapsed:    0.9s
[Parallel(n_jobs=-1)]: Done  13 tasks      | elapsed:    1.0s
[Parallel(n_jobs=-1)]: Done  14 tasks      | elapsed:    1.1s
[Parallel(n_jobs=-1)]: Done  15 tasks      | elaps

[Parallel(n_jobs=-1)]: Done 136 tasks      | elapsed:    3.7s
[Parallel(n_jobs=-1)]: Done 137 tasks      | elapsed:    3.7s
[Parallel(n_jobs=-1)]: Done 138 tasks      | elapsed:    3.8s
[Parallel(n_jobs=-1)]: Done 139 tasks      | elapsed:    3.8s
[Parallel(n_jobs=-1)]: Done 140 tasks      | elapsed:    3.8s
[Parallel(n_jobs=-1)]: Done 141 tasks      | elapsed:    3.8s
[Parallel(n_jobs=-1)]: Done 142 tasks      | elapsed:    3.8s
[Parallel(n_jobs=-1)]: Done 143 tasks      | elapsed:    3.8s
[Parallel(n_jobs=-1)]: Done 144 tasks      | elapsed:    3.9s
[Parallel(n_jobs=-1)]: Done 145 tasks      | elapsed:    3.9s
[Parallel(n_jobs=-1)]: Done 146 tasks      | elapsed:    3.9s
[Parallel(n_jobs=-1)]: Done 147 tasks      | elapsed:    3.9s
[Parallel(n_jobs=-1)]: Done 148 tasks      | elapsed:    4.0s
[Parallel(n_jobs=-1)]: Done 149 tasks      | elapsed:    4.0s
[Parallel(n_jobs=-1)]: Done 150 tasks      | elapsed:    4.0s
[Parallel(n_jobs=-1)]: Done 151 tasks      | elapsed:    4.0s
[Paralle

[Parallel(n_jobs=-1)]: Done 276 tasks      | elapsed:    6.7s
[Parallel(n_jobs=-1)]: Done 277 tasks      | elapsed:    6.7s
[Parallel(n_jobs=-1)]: Done 278 tasks      | elapsed:    6.8s
[Parallel(n_jobs=-1)]: Done 279 tasks      | elapsed:    6.8s
[Parallel(n_jobs=-1)]: Done 280 tasks      | elapsed:    6.8s
[Parallel(n_jobs=-1)]: Done 281 tasks      | elapsed:    6.8s
[Parallel(n_jobs=-1)]: Done 282 tasks      | elapsed:    6.9s
[Parallel(n_jobs=-1)]: Done 283 tasks      | elapsed:    6.9s
[Parallel(n_jobs=-1)]: Done 284 tasks      | elapsed:    7.0s
[Parallel(n_jobs=-1)]: Done 285 tasks      | elapsed:    7.0s
[Parallel(n_jobs=-1)]: Done 286 tasks      | elapsed:    7.0s
[Parallel(n_jobs=-1)]: Done 287 tasks      | elapsed:    7.0s
[Parallel(n_jobs=-1)]: Done 288 tasks      | elapsed:    7.0s
[Parallel(n_jobs=-1)]: Done 289 tasks      | elapsed:    7.0s
[Parallel(n_jobs=-1)]: Done 290 tasks      | elapsed:    7.1s
[Parallel(n_jobs=-1)]: Done 291 tasks      | elapsed:    7.1s
[Paralle

[Parallel(n_jobs=-1)]: Done 415 tasks      | elapsed:   10.2s
[Parallel(n_jobs=-1)]: Done 416 tasks      | elapsed:   10.2s
[Parallel(n_jobs=-1)]: Done 417 tasks      | elapsed:   10.2s
[Parallel(n_jobs=-1)]: Done 418 tasks      | elapsed:   10.3s
[Parallel(n_jobs=-1)]: Done 419 tasks      | elapsed:   10.3s
[Parallel(n_jobs=-1)]: Done 420 tasks      | elapsed:   11.5s
[Parallel(n_jobs=-1)]: Done 421 tasks      | elapsed:   11.5s
[Parallel(n_jobs=-1)]: Done 422 tasks      | elapsed:   11.5s
[Parallel(n_jobs=-1)]: Done 423 tasks      | elapsed:   11.5s
[Parallel(n_jobs=-1)]: Done 424 tasks      | elapsed:   11.5s
[Parallel(n_jobs=-1)]: Done 425 tasks      | elapsed:   11.6s
[Parallel(n_jobs=-1)]: Done 426 tasks      | elapsed:   11.6s
[Parallel(n_jobs=-1)]: Done 427 tasks      | elapsed:   11.7s
[Parallel(n_jobs=-1)]: Done 428 tasks      | elapsed:   11.7s
[Parallel(n_jobs=-1)]: Done 429 tasks      | elapsed:   11.7s
[Parallel(n_jobs=-1)]: Done 430 tasks      | elapsed:   11.8s
[Paralle

[Parallel(n_jobs=-1)]: Done 549 tasks      | elapsed:   14.6s
[Parallel(n_jobs=-1)]: Done 550 tasks      | elapsed:   14.6s
[Parallel(n_jobs=-1)]: Done 551 tasks      | elapsed:   14.6s
[Parallel(n_jobs=-1)]: Done 552 tasks      | elapsed:   14.7s
[Parallel(n_jobs=-1)]: Done 553 tasks      | elapsed:   14.7s
[Parallel(n_jobs=-1)]: Done 554 tasks      | elapsed:   14.7s
[Parallel(n_jobs=-1)]: Done 555 tasks      | elapsed:   14.7s
[Parallel(n_jobs=-1)]: Done 556 tasks      | elapsed:   14.8s
[Parallel(n_jobs=-1)]: Done 557 tasks      | elapsed:   14.8s
[Parallel(n_jobs=-1)]: Done 558 tasks      | elapsed:   14.8s
[Parallel(n_jobs=-1)]: Done 559 tasks      | elapsed:   14.8s
[Parallel(n_jobs=-1)]: Done 560 tasks      | elapsed:   14.8s
[Parallel(n_jobs=-1)]: Done 561 tasks      | elapsed:   14.8s
[Parallel(n_jobs=-1)]: Done 562 tasks      | elapsed:   14.9s
[Parallel(n_jobs=-1)]: Done 563 tasks      | elapsed:   14.9s
[Parallel(n_jobs=-1)]: Done 564 tasks      | elapsed:   14.9s
[Paralle

...

[Parallel(n_jobs=-1)]: Done 60240 tasks      | elapsed: 18.4min
[Parallel(n_jobs=-1)]: Done 60241 tasks      | elapsed: 18.4min
[Parallel(n_jobs=-1)]: Done 60242 tasks      | elapsed: 18.4min
[Parallel(n_jobs=-1)]: Done 60243 tasks      | elapsed: 18.4min
[Parallel(n_jobs=-1)]: Done 60244 tasks      | elapsed: 18.4min
[Parallel(n_jobs=-1)]: Done 60245 tasks      | elapsed: 18.4min
[Parallel(n_jobs=-1)]: Done 60246 tasks      | elapsed: 18.4min
[Parallel(n_jobs=-1)]: Done 60247 tasks      | elapsed: 18.4min
[Parallel(n_jobs=-1)]: Done 60248 tasks      | elapsed: 18.4min
[Parallel(n_jobs=-1)]: Done 60249 tasks      | elapsed: 18.4min
[Parallel(n_jobs=-1)]: Done 60250 tasks      | elapsed: 18.4min
[Parallel(n_jobs=-1)]: Done 60251 tasks      | elapsed: 18.4min
[Parallel(n_jobs=-1)]: Done 60252 tasks      | elapsed: 18.4min
[Parallel(n_jobs=-1)]: Done 60253 tasks      | elapsed: 18.4min
[Parallel(n_jobs=-1)]: Done 60254 tasks      | elapsed: 18.4min
[Parallel(n_jobs=-1)]: Done 60255 tasks 

[Parallel(n_jobs=-1)]: Done 60460 tasks      | elapsed: 18.4min
[Parallel(n_jobs=-1)]: Done 60461 tasks      | elapsed: 18.4min
[Parallel(n_jobs=-1)]: Done 60462 tasks      | elapsed: 18.4min
[Parallel(n_jobs=-1)]: Done 60463 tasks      | elapsed: 18.4min
[Parallel(n_jobs=-1)]: Done 60464 tasks      | elapsed: 18.4min
[Parallel(n_jobs=-1)]: Done 60465 tasks      | elapsed: 18.4min
[Parallel(n_jobs=-1)]: Done 60466 tasks      | elapsed: 18.4min
[Parallel(n_jobs=-1)]: Done 60467 tasks      | elapsed: 18.4min
[Parallel(n_jobs=-1)]: Done 60468 tasks      | elapsed: 18.4min
[Parallel(n_jobs=-1)]: Done 60469 tasks      | elapsed: 18.4min
[Parallel(n_jobs=-1)]: Done 60470 tasks      | elapsed: 18.4min
[Parallel(n_jobs=-1)]: Done 60471 tasks      | elapsed: 18.4min
[Parallel(n_jobs=-1)]: Done 60472 tasks      | elapsed: 18.4min
[Parallel(n_jobs=-1)]: Done 60473 tasks      | elapsed: 18.4min
[Parallel(n_jobs=-1)]: Done 60474 tasks      | elapsed: 18.4min
[Parallel(n_jobs=-1)]: Done 60475 tasks 

[Parallel(n_jobs=-1)]: Done 60611 tasks      | elapsed: 18.4min
[Parallel(n_jobs=-1)]: Done 60612 tasks      | elapsed: 18.4min
[Parallel(n_jobs=-1)]: Done 60613 tasks      | elapsed: 18.4min
[Parallel(n_jobs=-1)]: Done 60614 tasks      | elapsed: 18.4min
[Parallel(n_jobs=-1)]: Done 60615 tasks      | elapsed: 18.4min
[Parallel(n_jobs=-1)]: Done 60616 tasks      | elapsed: 18.4min
[Parallel(n_jobs=-1)]: Done 60617 tasks      | elapsed: 18.4min
[Parallel(n_jobs=-1)]: Done 60618 tasks      | elapsed: 18.4min
[Parallel(n_jobs=-1)]: Done 60619 tasks      | elapsed: 18.4min
[Parallel(n_jobs=-1)]: Done 60620 tasks      | elapsed: 18.4min
[Parallel(n_jobs=-1)]: Done 60621 tasks      | elapsed: 18.4min
[Parallel(n_jobs=-1)]: Done 60622 tasks      | elapsed: 18.4min
[Parallel(n_jobs=-1)]: Done 60623 tasks      | elapsed: 18.4min
[Parallel(n_jobs=-1)]: Done 60624 tasks      | elapsed: 18.4min
[Parallel(n_jobs=-1)]: Done 60625 tasks      | elapsed: 18.4min
[Parallel(n_jobs=-1)]: Done 60626 tasks 

[Parallel(n_jobs=-1)]: Done 60816 tasks      | elapsed: 18.4min
[Parallel(n_jobs=-1)]: Done 60817 tasks      | elapsed: 18.4min
[Parallel(n_jobs=-1)]: Done 60818 tasks      | elapsed: 18.4min
[Parallel(n_jobs=-1)]: Done 60819 tasks      | elapsed: 18.4min
[Parallel(n_jobs=-1)]: Done 60820 tasks      | elapsed: 18.4min
[Parallel(n_jobs=-1)]: Done 60821 tasks      | elapsed: 18.4min
[Parallel(n_jobs=-1)]: Done 60822 tasks      | elapsed: 18.4min
[Parallel(n_jobs=-1)]: Done 60823 tasks      | elapsed: 18.4min
[Parallel(n_jobs=-1)]: Done 60824 tasks      | elapsed: 18.4min
[Parallel(n_jobs=-1)]: Done 60825 tasks      | elapsed: 18.4min
[Parallel(n_jobs=-1)]: Done 60826 tasks      | elapsed: 18.4min
[Parallel(n_jobs=-1)]: Done 60827 tasks      | elapsed: 18.4min
[Parallel(n_jobs=-1)]: Done 60828 tasks      | elapsed: 18.4min
[Parallel(n_jobs=-1)]: Done 60829 tasks      | elapsed: 18.4min
[Parallel(n_jobs=-1)]: Done 60830 tasks      | elapsed: 18.4min
[Parallel(n_jobs=-1)]: Done 60831 tasks 

[Parallel(n_jobs=-1)]: Done 62220 tasks      | elapsed: 18.4min
[Parallel(n_jobs=-1)]: Done 62221 tasks      | elapsed: 18.4min
[Parallel(n_jobs=-1)]: Done 62222 tasks      | elapsed: 18.4min
[Parallel(n_jobs=-1)]: Done 62223 tasks      | elapsed: 18.4min
[Parallel(n_jobs=-1)]: Done 62224 tasks      | elapsed: 18.4min
[Parallel(n_jobs=-1)]: Done 62225 tasks      | elapsed: 18.4min
[Parallel(n_jobs=-1)]: Done 62226 tasks      | elapsed: 18.4min
[Parallel(n_jobs=-1)]: Done 62227 tasks      | elapsed: 18.4min
[Parallel(n_jobs=-1)]: Done 62228 tasks      | elapsed: 18.4min
[Parallel(n_jobs=-1)]: Done 62229 tasks      | elapsed: 18.4min
[Parallel(n_jobs=-1)]: Done 62230 tasks      | elapsed: 18.4min
[Parallel(n_jobs=-1)]: Done 62231 tasks      | elapsed: 18.4min
[Parallel(n_jobs=-1)]: Done 62232 tasks      | elapsed: 18.4min
[Parallel(n_jobs=-1)]: Done 62233 tasks      | elapsed: 18.4min
[Parallel(n_jobs=-1)]: Done 62234 tasks      | elapsed: 18.4min
[Parallel(n_jobs=-1)]: Done 62235 tasks 

In [6]:
impossible_fit = np.array(impossible_fit_list, np.float64)
with np.printoptions(precision=3, suppress=True):
    print('impossible fits : ', impossible_fit[np.where(impossible_fit[:,0] != 0),:].shape[1])
    print('proportion in CV and locations : ')
    print(impossible_fit[np.where(impossible_fit[:,0] != 0),:])

impossible fits :  1747
proportion in CV and locations : 
[[[  0.083   0.     91.   ]
  [  0.083   0.     90.   ]
  [  0.083   0.     89.   ]
  ...
  [  0.083 154.      1.   ]
  [  0.083 154.      2.   ]
  [  0.083 154.    114.   ]]]


In [7]:
for j,jmemb in enumerate(range(first_memb, last_memb)):
    memb_str = 'memb'+str(jmemb)
    nrealisation = 1 #because we separe every memb
    parameters_str = reg_name+"_"+season+"_"+cv_str+'_percent%i'%(percent_thresh)+'_daymin%i'%(duration_min)+"_ref%i-%i_"%(start_year, end_year)+memb_str
    varout1 = "HWMI"+"_"+parameters_str
    dirout = "/cnrm/pastel/USERS/lecestres/NO_SAVE/data/"+expname+"/"+memb_str+'/'+season+'/'+varout1+"/"
    if os.path.isdir(dirout):
        shutil.rmtree(dirout)
    os.makedirs(dirout)
    
    for i,iyear in enumerate(range(start_year, end_year+1)):
        #print iyear
        fileout=dirout+varout1+"_%i_%i.nc"%(iyear,iyear+1) #0%i01, monstart)
        print(fileout)
        if len(glob(fileout))==1:
            os.remove(fileout)
        fout=netCDF4.Dataset(fileout, "w")
        #fin=netCDF4.Dataset(targetflst[iyear])
        lat = fout.createDimension('lat', nlat)
        lon = fout.createDimension('lon', nlon) 
        rea = fout.createDimension('realisation', nrealisation) 
        timedim = fout.createDimension('time', None) 
        times = fout.createVariable('time', np.float64, ('time',)) 
        latitudes = fout.createVariable('lat', np.float32, ('lat',)) 
        longitudes = fout.createVariable('lon', np.float32,  ('lon',)) 
    
        # Time variable
        times.units = 'hours since 0001-01-01 00:00:00'  
        times.calendar = 'gregorian' 
        times[:]=date2num(datetime(iyear,season_start_day[0],season_start_day[1]), units = times.units, calendar = times.calendar) ####______HERE_____
    
        
        #varlat = getvarlat(fin)
        #varlon = getvarlon(fin)
        #latitudes[:] = fin.variables[varlat][:]
        #lonaux=fin.variables[varlon][:]
        latitudes[:] = lats_reg
        lonaux = lons_reg
        lonaux[lonaux<0]=lonaux[lonaux<0]+360
        longitudes[:] = lonaux
        latitudes.units = 'degree_north'  
        longitudes.units = 'degree_east' 
    
            
        # Create the HWMI 4-d variable
        HWMIfile = fout.createVariable(varout1, np.float32, ('time','realisation','lat','lon'))
        fout.description = 'HWMI index (Russo et al. 2014) for ' + season + ' computed in cross validation'
        fout.history = 'computed from python script by C.Prodhomme & S.Lecestre' + time.ctime(time.time())
        fout.source = 'HWMI for ' + expname
        latitudes.units = 'degree_north'  
        longitudes.units = 'degree_east' 
        HWMIfile.units = 'Probability'
        
        # Create the nb of days 4-d variable
        expercentfile = fout.createVariable("nbdaygtpercentpct", np.float32, ('time','realisation','lat','lon'))
        expercentfile.units = 'Number of days'  
        
        
        # Create the nb of days 4-d variable
        DDthresholdfile = fout.createVariable("DDthreshold", np.float32, ('time','realisation','lat','lon'))
        DDthresholdfile.units = 'degree'
        
        # Create the SSTmean 4-d variable
        SSTmeanfile = fout.createVariable('sst_mean', np.float32, ('time', 'realisation', 'lat', 'lon'))
        SSTmeanfile.units = 'degree'
        
        # Write the HWMI variable
        HWMIaux=HWMI[i:i+1,j:j+1,:,:]
        HWMIfile[0:1,0:1,:,:]=HWMIaux
        
        # Write the number of days
        exedaux=ndayexedthreshold[i:i+1,j:j+1,:,:]
        expercentfile[0:1,0:1,:,:]=exedaux 
        
        # Write the DDthreshold
        exedaux=DDthreshold[i:i+1,j:j+1,:,:]
        DDthresholdfile[0:1,0:1,:,:]=exedaux 
        
        # Write the SSTmean
        SSTaux = sstMeanarray[i:i+1,j:j+1,:,:]
        SSTmeanfile[0:1,0:1,:,:]=SSTaux
    
        
        fout.close()
        #fin.close()

/cnrm/pastel/USERS/lecestres/NO_SAVE/data/sst_retroprevision_sys7/memb0/DJF/HWMI_global_DJF_CV_percent95_daymin5_ref1993-2016_memb0/HWMI_global_DJF_CV_percent95_daymin5_ref1993-2016_memb0_1993_1994.nc
/cnrm/pastel/USERS/lecestres/NO_SAVE/data/sst_retroprevision_sys7/memb0/DJF/HWMI_global_DJF_CV_percent95_daymin5_ref1993-2016_memb0/HWMI_global_DJF_CV_percent95_daymin5_ref1993-2016_memb0_1994_1995.nc
/cnrm/pastel/USERS/lecestres/NO_SAVE/data/sst_retroprevision_sys7/memb0/DJF/HWMI_global_DJF_CV_percent95_daymin5_ref1993-2016_memb0/HWMI_global_DJF_CV_percent95_daymin5_ref1993-2016_memb0_1995_1996.nc
/cnrm/pastel/USERS/lecestres/NO_SAVE/data/sst_retroprevision_sys7/memb0/DJF/HWMI_global_DJF_CV_percent95_daymin5_ref1993-2016_memb0/HWMI_global_DJF_CV_percent95_daymin5_ref1993-2016_memb0_1996_1997.nc
/cnrm/pastel/USERS/lecestres/NO_SAVE/data/sst_retroprevision_sys7/memb0/DJF/HWMI_global_DJF_CV_percent95_daymin5_ref1993-2016_memb0/HWMI_global_DJF_CV_percent95_daymin5_ref1993-2016_memb0_1997_199

/cnrm/pastel/USERS/lecestres/NO_SAVE/data/sst_retroprevision_sys7/memb1/DJF/HWMI_global_DJF_CV_percent95_daymin5_ref1993-2016_memb1/HWMI_global_DJF_CV_percent95_daymin5_ref1993-2016_memb1_2011_2012.nc
/cnrm/pastel/USERS/lecestres/NO_SAVE/data/sst_retroprevision_sys7/memb1/DJF/HWMI_global_DJF_CV_percent95_daymin5_ref1993-2016_memb1/HWMI_global_DJF_CV_percent95_daymin5_ref1993-2016_memb1_2012_2013.nc
/cnrm/pastel/USERS/lecestres/NO_SAVE/data/sst_retroprevision_sys7/memb1/DJF/HWMI_global_DJF_CV_percent95_daymin5_ref1993-2016_memb1/HWMI_global_DJF_CV_percent95_daymin5_ref1993-2016_memb1_2013_2014.nc
/cnrm/pastel/USERS/lecestres/NO_SAVE/data/sst_retroprevision_sys7/memb1/DJF/HWMI_global_DJF_CV_percent95_daymin5_ref1993-2016_memb1/HWMI_global_DJF_CV_percent95_daymin5_ref1993-2016_memb1_2014_2015.nc
/cnrm/pastel/USERS/lecestres/NO_SAVE/data/sst_retroprevision_sys7/memb1/DJF/HWMI_global_DJF_CV_percent95_daymin5_ref1993-2016_memb1/HWMI_global_DJF_CV_percent95_daymin5_ref1993-2016_memb1_2015_201

In [8]:
lats_reg, lons_reg

(masked_array(data=[ 89.5,  88.5,  87.5,  86.5,  85.5,  84.5,  83.5,  82.5,
                     81.5,  80.5,  79.5,  78.5,  77.5,  76.5,  75.5,  74.5,
                     73.5,  72.5,  71.5,  70.5,  69.5,  68.5,  67.5,  66.5,
                     65.5,  64.5,  63.5,  62.5,  61.5,  60.5,  59.5,  58.5,
                     57.5,  56.5,  55.5,  54.5,  53.5,  52.5,  51.5,  50.5,
                     49.5,  48.5,  47.5,  46.5,  45.5,  44.5,  43.5,  42.5,
                     41.5,  40.5,  39.5,  38.5,  37.5,  36.5,  35.5,  34.5,
                     33.5,  32.5,  31.5,  30.5,  29.5,  28.5,  27.5,  26.5,
                     25.5,  24.5,  23.5,  22.5,  21.5,  20.5,  19.5,  18.5,
                     17.5,  16.5,  15.5,  14.5,  13.5,  12.5,  11.5,  10.5,
                      9.5,   8.5,   7.5,   6.5,   5.5,   4.5,   3.5,   2.5,
                      1.5,   0.5,  -0.5,  -1.5,  -2.5,  -3.5,  -4.5,  -5.5,
                     -6.5,  -7.5,  -8.5,  -9.5, -10.5, -11.5, -12.5, -13.5,
            

In [9]:
for j,jmemb in enumerate(range(first_memb, last_memb)):
    nrealisation = 1
    memb_str = 'memb'+str(jmemb)
    parameters_str = reg_name+"_"+season+"_"+cv_str+'_percent%i'%(percent_thresh)+'_daymin%i'%(duration_min)+"_ref%i-%i_"%(start_year, end_year)+memb_str
    varout1 = "subHW_"+parameters_str
    dirout = "/cnrm/pastel/USERS/lecestres/NO_SAVE/data/"+expname+"/"+memb_str+'/'+season+'/'+varout1+"/"
    
    if os.path.isdir(dirout):
        shutil.rmtree(dirout)
    os.makedirs(dirout)
    
    for i,iyear in enumerate(range(start_year, end_year+1)):
        #print iyear
        fileout=dirout+varout1+"_%i_%i.nc"%(iyear,iyear+1) #0%i01, monstart)
        print(fileout)
        if len(glob(fileout))==1:
            os.remove(fileout)
        fout=netCDF4.Dataset(fileout, "w")
        #fin=netCDF4.Dataset(targetflst[iyear])
        lat = fout.createDimension('lat', nlat)
        lon = fout.createDimension('lon', nlon) 
        rea = fout.createDimension('realisation', nrealisation) 
        timedim = fout.createDimension('time', None) 
        times = fout.createVariable('time', np.float64, ('time',)) 
        latitudes = fout.createVariable('lat', np.float32, ('lat',)) 
        longitudes = fout.createVariable('lon', np.float32,  ('lon',)) 
    
        # Time variable
        times.units = 'hours since 0001-01-01 00:00:00'  
        times.calendar = 'gregorian' 
        times[:]=date2num(datetime((iyear),season_start_day[0],season_start_day[1]), units = times.units, calendar = times.calendar)
        
        #varlat = getvarlat(fin)
        #varlon = getvarlon(fin)
        #latitudes[:] = fin.variables[varlat][:]
        #lonaux=fin.variables[varlon][:]
        
        latitudes[:] = lats_reg
        lonaux = lons_reg
        lonaux[lonaux<0]=lonaux[lonaux<0]+360
        longitudes[:] = lonaux
        latitudes.units = 'degree_north'  
        longitudes.units = 'degree_east' 
        
        
        
        # create the variable with all the sub Heat Waves
        fitsubHWfile = fout.createVariable("fit"+varout1, np.float32, ('time','realisation', 'lat','lon'))
        fitsubHWfile.units = 'Probability'
        #print(fitsubHWarray[i,:(ndayseas),:,:,:].shape)
        fitsubHWarrayaux = fitsubHWarray[i,0:(ndayseas),j:j+1,:,:]
        #print(fitsubHWarrayaux.shape)
        #print(fitsubHWfile.shape)
        fitsubHWfile[0:(ndayseas),0:1,:,:]=fitsubHWarrayaux
        
        
            # create the variable with all the sub Heat Waves
        subHWfile = fout.createVariable(varout1, np.float32, ('time','realisation', 'lat','lon'))
        subHWfile.units = 'degree'
        subHWarrayaux = subHWarray[i,:(ndayseas),j:j+1,:,:]
        #print(subHWfile[0:(ndayseas),:,:,:].shape)
        subHWfile[0:(ndayseas),0:1,:,:]=subHWarrayaux
           
        fout.close()
        #fin.close()

/cnrm/pastel/USERS/lecestres/NO_SAVE/data/sst_retroprevision_sys7/memb0/DJF/subHW_global_DJF_CV_percent95_daymin5_ref1993-2016_memb0/subHW_global_DJF_CV_percent95_daymin5_ref1993-2016_memb0_1993_1994.nc
/cnrm/pastel/USERS/lecestres/NO_SAVE/data/sst_retroprevision_sys7/memb0/DJF/subHW_global_DJF_CV_percent95_daymin5_ref1993-2016_memb0/subHW_global_DJF_CV_percent95_daymin5_ref1993-2016_memb0_1994_1995.nc
/cnrm/pastel/USERS/lecestres/NO_SAVE/data/sst_retroprevision_sys7/memb0/DJF/subHW_global_DJF_CV_percent95_daymin5_ref1993-2016_memb0/subHW_global_DJF_CV_percent95_daymin5_ref1993-2016_memb0_1995_1996.nc
/cnrm/pastel/USERS/lecestres/NO_SAVE/data/sst_retroprevision_sys7/memb0/DJF/subHW_global_DJF_CV_percent95_daymin5_ref1993-2016_memb0/subHW_global_DJF_CV_percent95_daymin5_ref1993-2016_memb0_1996_1997.nc
/cnrm/pastel/USERS/lecestres/NO_SAVE/data/sst_retroprevision_sys7/memb0/DJF/subHW_global_DJF_CV_percent95_daymin5_ref1993-2016_memb0/subHW_global_DJF_CV_percent95_daymin5_ref1993-2016_memb

/cnrm/pastel/USERS/lecestres/NO_SAVE/data/sst_retroprevision_sys7/memb1/DJF/subHW_global_DJF_CV_percent95_daymin5_ref1993-2016_memb1/subHW_global_DJF_CV_percent95_daymin5_ref1993-2016_memb1_2010_2011.nc
/cnrm/pastel/USERS/lecestres/NO_SAVE/data/sst_retroprevision_sys7/memb1/DJF/subHW_global_DJF_CV_percent95_daymin5_ref1993-2016_memb1/subHW_global_DJF_CV_percent95_daymin5_ref1993-2016_memb1_2011_2012.nc
/cnrm/pastel/USERS/lecestres/NO_SAVE/data/sst_retroprevision_sys7/memb1/DJF/subHW_global_DJF_CV_percent95_daymin5_ref1993-2016_memb1/subHW_global_DJF_CV_percent95_daymin5_ref1993-2016_memb1_2012_2013.nc
/cnrm/pastel/USERS/lecestres/NO_SAVE/data/sst_retroprevision_sys7/memb1/DJF/subHW_global_DJF_CV_percent95_daymin5_ref1993-2016_memb1/subHW_global_DJF_CV_percent95_daymin5_ref1993-2016_memb1_2013_2014.nc
/cnrm/pastel/USERS/lecestres/NO_SAVE/data/sst_retroprevision_sys7/memb1/DJF/subHW_global_DJF_CV_percent95_daymin5_ref1993-2016_memb1/subHW_global_DJF_CV_percent95_daymin5_ref1993-2016_memb